In [1]:
import requests
import pandas as pd
import time
from concurrent.futures import ThreadPoolExecutor, as_completed

url = "https://smdbu2pjz6.execute-api.us-east-1.amazonaws.com/produce"

# ---------- RETRY FUNCTION ----------
def send_event(event, max_retries=5):
    attempt = 0
    while attempt < max_retries:
        try:
            r = requests.post(url, json=event, timeout=5)
            if r.status_code == 200:
                return True
            else:
                print(f"[Retry {attempt+1}] Status {r.status_code}")
        except Exception as e:
            print(f"[Retry {attempt+1}] Exception: {e}")

        attempt += 1
        time.sleep(2 ** attempt * 0.1)

    print("Failed:", event.get("Booking_ID", "Unknown"))
    return False


# ---------- WORKER FUNCTION ----------
def worker(index_row):
    i, row = index_row
    success = send_event(row)
    if success:
        return f"Sent event {i}: Booking_ID={row.get('Booking_ID')}"
    else:
        return f"FAILED event {i}"


# ---------- READ CSV ----------
csv_file = "final_ride_bookings.csv"
df = pd.read_csv(csv_file)

# convert all to string, blanks instead of NaN
df = df.astype(str).fillna("")

records = df.to_dict(orient="records")


# ---------- PARALLEL SEND ----------
MAX_THREADS = 10   # sweet spot

start_time = time.time()

with ThreadPoolExecutor(max_workers=MAX_THREADS) as executor:
    futures = [
        executor.submit(worker, (i, row))
        for i, row in enumerate(records, start=1)
    ]

    for future in as_completed(futures):
        print(future.result())

end_time = time.time()

print(f"Finished in {(end_time - start_time)/60:.2f} minutes")


Sent event 9: Booking_ID=CNR4510807
Sent event 10: Booking_ID=CNR7721892
Sent event 1: Booking_ID=CNR5884300
Sent event 2: Booking_ID=CNR1326809
Sent event 7: Booking_ID=CNR2002539
Sent event 4: Booking_ID=CNR8906825
Sent event 8: Booking_ID=CNR6568000
Sent event 5: Booking_ID=CNR1950162
Sent event 6: Booking_ID=CNR4096693
Sent event 11: Booking_ID=CNR9070334
Sent event 13: Booking_ID=CNR4386945
Sent event 3: Booking_ID=CNR8494506
Sent event 14: Booking_ID=CNR2987763
Sent event 15: Booking_ID=CNR8962232
Sent event 12: Booking_ID=CNR9551927
Sent event 17: Booking_ID=CNR3221338
Sent event 18: Booking_ID=CNR6739317
Sent event 16: Booking_ID=CNR2390352
Sent event 19: Booking_ID=CNR6126048
Sent event 20: Booking_ID=CNR9465840
Sent event 22: Booking_ID=CNR7911434
Sent event 23: Booking_ID=CNR6178330
Sent event 21: Booking_ID=CNR9843229
Sent event 24: Booking_ID=CNR5309981
Sent event 25: Booking_ID=CNR2978950
Sent event 29: Booking_ID=CNR9834201
Sent event 26: Booking_ID=CNR2806943
Sent event